In [1]:
import grpc
import tensorflow as tf
from tensorflow_serving.apis import predict_pb2, prediction_service_pb2_grpc

2025-02-23 18:58:00.298998: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2025-02-23 18:58:00.299032: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
host="localhost:8500"
channel = grpc.insecure_channel(host)
stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)
stub

In [10]:
from PIL import Image
import numpy as np

def read_image(path):
    with Image.open(path) as img:
        img = img.resize((299, 299), Image.NEAREST)
    return img

def preprocess_input(x):
    x = x / 127.5
    x -= 1.
    return x

img = read_image("/workspaces/k8deployment/data/test/skirt/0558b2c5-be00-49de-b27f-8c88114ac36f.jpg")
X = np.array([img])

In [11]:
X.shape
tf.make_tensor_proto(X, dtype=float, shape=X.shape)

dtype: DT_FLOAT
tensor_shape {
  dim {
    size: 1
  }
  dim {
    size: 299
  }
  dim {
    size: 299
  }
  dim {
    size: 3
  }
}
tensor_content: "\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000kC\000\000QC\000\0008C\000\000hC\000\000NC\000\0005C\000\000^C\000\000DC\000\000+C\000\000[C\000\000AC\000\000(C\000\000\\C\000\000BC\000\000)C\000\000`C\000\000FC\000\000-C\000\000bC\000\000HC\000\000/C\000\000fC\000\000LC\000\0003C\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000gC\000\000MC\000\0004C\000\000iC\000\000OC\000\0006C\000\000nC\000\000TC\000\000;C\000\000lC\000\000RC\000\0009C\000\000fC\000\000LC\000\0003C\000\000nC\000\000TC\000\000;C\000\000dC\000\000JC\000\0001C\000\000lC\000\000RC\000\0009C\000\000nC\000\000TC\000\000;C\000\000hC\000\000NC\000\0005C\000\000mC\000\000SC\000\000:C\000\000`C\000\000FC\000\000-C\000\000iC\000\000OC\000\0006C\000\000fC\000\000LC\000\0003C\000\000kC\000\000QC\000\0008C\000\000kC\000\000QC\000\0008C\000\000m

In [12]:
pb_request = predict_pb2.PredictRequest()
pb_request.model_spec.name = "clothes-classifier"
pb_request.model_spec.signature_name = "serving_default"
pb_request.inputs['input_2'].CopyFrom(tf.make_tensor_proto(X, dtype=float, shape=X.shape))

pb_request

model_spec {
  name: "clothes-classifier"
  signature_name: "serving_default"
}
inputs {
  key: "input_2"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 299
      }
      dim {
        size: 299
      }
      dim {
        size: 3
      }
    }
    tensor_content: "\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000kC\000\000QC\000\0008C\000\000hC\000\000NC\000\0005C\000\000^C\000\000DC\000\000+C\000\000[C\000\000AC\000\000(C\000\000\\C\000\000BC\000\000)C\000\000`C\000\000FC\000\000-C\000\000bC\000\000HC\000\000/C\000\000fC\000\000LC\000\0003C\000\000kC\000\000QC\000\0008C\000\000lC\000\000RC\000\0009C\000\000gC\000\000MC\000\0004C\000\000iC\000\000OC\000\0006C\000\000nC\000\000TC\000\000;C\000\000lC\000\000RC\000\0009C\000\000fC\000\000LC\000\0003C\000\000nC\000\000TC\000\000;C\000\000dC\000\000JC\000\0001C\000\000lC\000\000RC\000\0009C\000\000nC\000\000TC\000\000;C\000\000hC\000\000NC\000\0005C\000\000m

In [13]:
pb_response = stub.Predict(pb_request, timeout=20.0)

In [14]:
pb_response

outputs {
  key: "dense_1"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 10
      }
    }
    float_val: 65.4022216796875
    float_val: 12.036943435668945
    float_val: -75.39482879638672
    float_val: 26.65360450744629
    float_val: -40.73039245605469
    float_val: -46.05611038208008
    float_val: 20.971534729003906
    float_val: -33.63168716430664
    float_val: -3.0841426849365234
    float_val: 31.569238662719727
  }
}
model_spec {
  name: "clothes-classifier"
  version {
    value: 1
  }
  signature_name: "serving_default"
}

In [15]:
classes = [
    "dress",
    "hat",
    "longsleeve",
    "outwear",
    "pants",
    "shirts",
    "shoes",
    "shorts",
    "skirts",
    "t-shirt"
]

In [17]:
dict(zip(classes, pb_response.outputs['dense_1'].float_val))

{'dress': 65.4022216796875,
 'hat': 12.036943435668945,
 'longsleeve': -75.39482879638672,
 'outwear': 26.65360450744629,
 'pants': -40.73039245605469,
 'shirts': -46.05611038208008,
 'shoes': 20.971534729003906,
 'shorts': -33.63168716430664,
 'skirts': -3.0841426849365234,
 't-shirt': 31.569238662719727}